In [0]:
!pip install torch torchvision tqdm
import torch, os
import torchvision
import torchvision.transforms as transforms
from tqdm import tqdm
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim

    100% |████████████████████████████████| 519.5MB 31kB/s 
tcmalloc: large alloc 1073750016 bytes == 0x5968e000 @  0x7fb3ed1f31c4 0x46d6a4 0x5fcbcc 0x4c494d 0x54f3c4 0x553aaf 0x54e4c8 0x54f4f6 0x553aaf 0x54efc1 0x54f24d 0x553aaf 0x54efc1 0x54f24d 0x553aaf 0x54efc1 0x54f24d 0x551ee0 0x54e4c8 0x54f4f6 0x553aaf 0x54efc1 0x54f24d 0x551ee0 0x54efc1 0x54f24d 0x551ee0 0x54e4c8 0x54f4f6 0x553aaf 0x54e4c8
    100% |████████████████████████████████| 61kB 1.7MB/s 
    100% |████████████████████████████████| 51kB 11.7MB/s 
    100% |████████████████████████████████| 2.0MB 2.9MB/s 
  Found existing installation: Pillow 4.0.0
    Uninstalling Pillow-4.0.0:
      Successfully uninstalled Pillow-4.0.0


In [0]:
transform = transforms.Compose([transforms.ToTensor(),])

trainset = torchvision.datasets.CIFAR10(root='./data', train=True,
                                        download=True, transform=transform)
trainloader = torch.utils.data.DataLoader(trainset, batch_size=4,
                                          shuffle=True, num_workers=2)

testset = torchvision.datasets.CIFAR10(root='./data', train=False,
                                       download=True, transform=transform)
testloader = torch.utils.data.DataLoader(testset, batch_size=4,
                                         shuffle=False, num_workers=2)

classes = ('plane', 'car', 'bird', 'cat',
           'deer', 'dog', 'frog', 'horse', 'ship', 'truck')

Files already downloaded and verified


In [0]:
def train(epoch, trainloader, optimizer, criterion):
    running_loss = 0.0
    for i, data in enumerate(tqdm(trainloader), 0):
        # get the inputs
        inputs, labels = data
        if torch.cuda.is_available():
            inputs, labels = inputs.cuda(), labels.cuda()

        # zero the parameter gradients
        optimizer.zero_grad()

        # forward + backward + optimize
        outputs = net(inputs)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()

        # print statistics
        running_loss += loss.item()

    print('epoch %d training loss: %.3f' %
            (epoch + 1, running_loss / (len(trainloader))))

In [0]:
def test(testloader, model):
    correct = 0
    total = 0
    with torch.no_grad():
        for data in tqdm(testloader):
            images, labels = data
            if torch.cuda.is_available():
                images, labels = images.cuda(), labels.cuda()        
            outputs = net(images)
            _, predicted = torch.max(outputs.data, 1)
            total += labels.size(0)
            correct += (predicted == labels).sum().item()

    print('Accuracy of the network on the 10000 test images: %d %%' % (
                                    100 * correct / total))

In [0]:
def classwise_test(testloader, model):
########################################################################
# class-wise accuracy

    class_correct = list(0. for i in range(10))
    class_total = list(0. for i in range(10))
    with torch.no_grad():
        for data in tqdm(testloader):
            images, labels = data
            if torch.cuda.is_available():
                images, labels = images.cuda(), labels.cuda()        
            outputs = net(images)
            _, predicted = torch.max(outputs, 1)
            c = (predicted == labels).squeeze()
            for i in range(4):
                label = labels[i]
                class_correct[label] += c[i].item()
                class_total[label] += 1

    for i in range(10):
        print('Accuracy of %5s : %2d %%' % (
            classes[i], 100 * class_correct[i] / class_total[i]))


In [34]:
num_epochs = 5
learning_rate = 0.001
class Net(nn.Module):
    def __init__(self):
        super(Net, self).__init__()
        
        self.conv1 = nn.Conv2d(in_channels=3, out_channels=128, kernel_size=5)#32-5+1=28
        self.pool1 = nn.MaxPool2d(kernel_size=2, stride=2)#14
        self.conv2 = nn.Conv2d(in_channels=128, out_channels=256, kernel_size=3)#14-3+1=12
        self.pool2 = nn.MaxPool2d(kernel_size=2, stride=2)#6
        self.conv3 = nn.Conv2d(in_channels=256, out_channels=512, kernel_size=3)#6-3+1=4
        self.pool3 = nn.MaxPool2d(kernel_size=2, stride=2)#2
        self.conv4 = nn.Conv2d(in_channels=512, out_channels=1024, kernel_size=1)#2
        self.pool4= nn.MaxPool2d(kernel_size=2, stride=2)#1
        self.fc1 = nn.Linear(in_features=1024*1*1, out_features=512)
        self.fc2 = nn.Linear(in_features=512, out_features=256)
        self.fc3 = nn.Linear(in_features=256, out_features=10)


    def forward(self, x):
        x = self.pool1(F.relu(self.conv1(x)))
        x = self.pool2(F.relu(self.conv2(x)))
        x = self.pool3(F.relu(self.conv3(x)))
        x = self.pool4(F.relu(self.conv4(x)))
        
        x = x.view(-1, 1024*1*1)
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        x = self.fc3(x)
        return x
net = Net()
# transfer the model to GPU
if torch.cuda.is_available():
    net = net.cuda()
    print("Using GPU")

criterion = nn.CrossEntropyLoss()
optimizer = optim.SGD(net.parameters(), lr=learning_rate, momentum=0.9)

print('Start Training')
os.makedirs('./models', exist_ok=True)

for epoch in range(num_epochs):  # loop over the dataset multiple times
    print('epoch ', epoch + 1)
    train(epoch, trainloader, optimizer, criterion)
    test(testloader, net)
    classwise_test(testloader, net)
    torch.save(net.state_dict(), './models/model-'+str(epoch)+'.pth')

print('Finished Training')




  0%|          | 0/12500 [00:00<?, ?it/s]

Using GPU
Start Training
epoch  1





  0%|          | 3/12500 [00:00<07:15, 28.67it/s]


  0%|          | 11/12500 [00:00<03:58, 52.31it/s]


  0%|          | 20/12500 [00:00<03:20, 62.33it/s]


  0%|          | 29/12500 [00:00<03:04, 67.56it/s]


  0%|          | 37/12500 [00:00<02:59, 69.36it/s]


  0%|          | 45/12500 [00:00<02:57, 70.06it/s]


  0%|          | 54/12500 [00:00<02:53, 71.73it/s]


  0%|          | 62/12500 [00:00<02:52, 71.98it/s]


  1%|          | 70/12500 [00:00<02:51, 72.68it/s]


  1%|          | 78/12500 [00:01<02:49, 73.35it/s]


  1%|          | 86/12500 [00:01<02:48, 73.58it/s]


  1%|          | 94/12500 [00:01<02:47, 73.93it/s]


  1%|          | 102/12500 [00:01<02:47, 74.01it/s]


  1%|          | 110/12500 [00:01<02:47, 74.09it/s]


  1%|          | 119/12500 [00:01<02:45, 74.63it/s]


  1%|          | 127/12500 [00:01<02:45, 74.74it/s]


  1%|          | 135/12500 [00:01<02:45, 74.69it/s]


  1%|          | 143/12500 [00:01<02:45, 74.66it/s]


  1%|          | 151/12500 [00:02<02:4

epoch 1 training loss: 2.053





  0%|          | 1/2500 [00:00<05:02,  8.26it/s]


  1%|          | 14/2500 [00:00<00:38, 63.78it/s]


  1%|          | 26/2500 [00:00<00:30, 80.70it/s]


  1%|▏         | 37/2500 [00:00<00:28, 87.16it/s]


  2%|▏         | 51/2500 [00:00<00:25, 96.07it/s]


  3%|▎         | 65/2500 [00:00<00:23, 102.89it/s]


  3%|▎         | 81/2500 [00:00<00:22, 109.84it/s]


  4%|▍         | 95/2500 [00:00<00:21, 112.69it/s]


  4%|▍         | 109/2500 [00:00<00:20, 115.20it/s]


  5%|▍         | 123/2500 [00:01<00:20, 116.97it/s]


  5%|▌         | 136/2500 [00:01<00:20, 118.04it/s]


  6%|▌         | 149/2500 [00:01<00:19, 118.45it/s]


  6%|▋         | 162/2500 [00:01<00:19, 118.60it/s]


  7%|▋         | 175/2500 [00:01<00:19, 119.00it/s]


  8%|▊         | 188/2500 [00:01<00:19, 118.72it/s]


  8%|▊         | 201/2500 [00:01<00:19, 118.68it/s]


  9%|▊         | 215/2500 [00:01<00:19, 119.71it/s]


  9%|▉         | 229/2500 [00:01<00:18, 120.46it/s]


 10%|▉         | 242/2500 [00:02<00:18,

...

epoch 5 training loss: 0.850





  0%|          | 1/2500 [00:00<05:18,  7.84it/s]


  0%|          | 10/2500 [00:00<00:59, 41.87it/s]


  1%|          | 17/2500 [00:00<00:50, 49.45it/s]


  1%|          | 24/2500 [00:00<00:46, 53.61it/s]


  1%|▏         | 32/2500 [00:00<00:42, 58.16it/s]


  2%|▏         | 39/2500 [00:00<00:40, 60.06it/s]


  2%|▏         | 46/2500 [00:00<00:39, 61.36it/s]


  2%|▏         | 54/2500 [00:00<00:38, 63.52it/s]


  3%|▎         | 63/2500 [00:00<00:37, 65.72it/s]


  3%|▎         | 72/2500 [00:01<00:35, 67.65it/s]


  3%|▎         | 81/2500 [00:01<00:34, 69.23it/s]


  4%|▎         | 90/2500 [00:01<00:34, 70.44it/s]


  4%|▍         | 99/2500 [00:01<00:34, 70.37it/s]


  4%|▍         | 108/2500 [00:01<00:33, 71.56it/s]


  5%|▍         | 120/2500 [00:01<00:32, 74.34it/s]


  5%|▌         | 132/2500 [00:01<00:30, 76.61it/s]


  6%|▌         | 142/2500 [00:01<00:30, 76.23it/s]


  6%|▌         | 151/2500 [00:01<00:31, 75.77it/s]


  6%|▋         | 160/2500 [00:02<00:30, 75.49it/s]


  7%

Accuracy of the network on the 10000 test images: 69 %





  0%|          | 1/2500 [00:00<06:11,  6.73it/s]


  0%|          | 9/2500 [00:00<01:09, 35.69it/s]


  1%|          | 18/2500 [00:00<00:48, 50.81it/s]


  1%|          | 28/2500 [00:00<00:40, 61.04it/s]


  2%|▏         | 42/2500 [00:00<00:32, 74.65it/s]


  2%|▏         | 53/2500 [00:00<00:30, 79.44it/s]


  2%|▏         | 62/2500 [00:00<00:31, 78.54it/s]


  3%|▎         | 71/2500 [00:00<00:31, 77.69it/s]


  3%|▎         | 80/2500 [00:01<00:31, 76.95it/s]


  4%|▎         | 88/2500 [00:01<00:31, 76.32it/s]


  4%|▍         | 98/2500 [00:01<00:30, 77.72it/s]


  4%|▍         | 108/2500 [00:01<00:30, 78.82it/s]


  5%|▍         | 117/2500 [00:01<00:30, 79.06it/s]


  5%|▌         | 126/2500 [00:01<00:30, 78.96it/s]


  5%|▌         | 135/2500 [00:01<00:30, 78.77it/s]


  6%|▌         | 144/2500 [00:01<00:29, 78.87it/s]


  6%|▌         | 153/2500 [00:01<00:29, 79.00it/s]


  7%|▋         | 165/2500 [00:02<00:28, 80.73it/s]


  7%|▋         | 178/2500 [00:02<00:28, 82.87it/s]


  8

Accuracy of plane : 75 %
Accuracy of   car : 87 %
Accuracy of  bird : 51 %
Accuracy of   cat : 59 %
Accuracy of  deer : 60 %
Accuracy of   dog : 46 %
Accuracy of  frog : 76 %
Accuracy of horse : 82 %
Accuracy of  ship : 85 %
Accuracy of truck : 66 %
Finished Training


In [35]:
print("Epoch 6 to 10")
for epoch in range(5,10):  # loop over the dataset multiple times
    print('epoch ', epoch + 1)
    train(epoch, trainloader, optimizer, criterion)
    test(testloader, net)
    classwise_test(testloader, net)
    torch.save(net.state_dict(), './models/model-'+str(epoch)+'.pth')

print('Finished Training')




  0%|          | 0/12500 [00:00<?, ?it/s]

Epoch 6 to 10
epoch  6





  0%|          | 1/12500 [00:00<23:01,  9.05it/s]


  0%|          | 7/12500 [00:00<06:14, 33.38it/s]


  0%|          | 13/12500 [00:00<05:03, 41.08it/s]


  0%|          | 19/12500 [00:00<04:35, 45.35it/s]


  0%|          | 25/12500 [00:00<04:19, 48.11it/s]


  0%|          | 31/12500 [00:00<04:10, 49.76it/s]


  0%|          | 37/12500 [00:00<04:05, 50.85it/s]


  0%|          | 44/12500 [00:00<03:57, 52.38it/s]


  0%|          | 50/12500 [00:00<03:58, 52.17it/s]


  0%|          | 57/12500 [00:01<03:53, 53.22it/s]


  1%|          | 63/12500 [00:01<03:52, 53.61it/s]


  1%|          | 70/12500 [00:01<03:47, 54.74it/s]


  1%|          | 77/12500 [00:01<03:44, 55.31it/s]


  1%|          | 84/12500 [00:01<03:43, 55.62it/s]


  1%|          | 91/12500 [00:01<03:41, 56.05it/s]


  1%|          | 98/12500 [00:01<03:40, 56.34it/s]


  1%|          | 105/12500 [00:01<03:40, 56.26it/s]


  1%|          | 111/12500 [00:01<03:39, 56.39it/s]


  1%|          | 117/12500 [00:02<03:39, 56

epoch 6 training loss: 0.703





  0%|          | 1/2500 [00:00<07:51,  5.30it/s]


  0%|          | 8/2500 [00:00<01:32, 26.84it/s]


  1%|          | 16/2500 [00:00<01:02, 39.85it/s]


  1%|          | 25/2500 [00:00<00:50, 48.76it/s]


  1%|▏         | 33/2500 [00:00<00:46, 53.62it/s]


  2%|▏         | 42/2500 [00:00<00:42, 57.88it/s]


  2%|▏         | 53/2500 [00:00<00:38, 63.73it/s]


  3%|▎         | 66/2500 [00:00<00:34, 70.71it/s]


  3%|▎         | 79/2500 [00:01<00:31, 75.92it/s]


  4%|▎         | 90/2500 [00:01<00:31, 75.32it/s]


  4%|▍         | 100/2500 [00:01<00:31, 75.58it/s]


  4%|▍         | 109/2500 [00:01<00:32, 74.04it/s]


  5%|▍         | 117/2500 [00:01<00:32, 74.45it/s]


  5%|▌         | 126/2500 [00:01<00:31, 74.97it/s]


  6%|▌         | 138/2500 [00:01<00:30, 77.51it/s]


  6%|▌         | 152/2500 [00:01<00:29, 80.74it/s]


  7%|▋         | 163/2500 [00:01<00:28, 82.11it/s]


  7%|▋         | 174/2500 [00:02<00:28, 81.06it/s]


  7%|▋         | 184/2500 [00:02<00:28, 80.74it/s]


  

...

epoch 10 training loss: 0.304





  0%|          | 1/2500 [00:00<04:27,  9.34it/s]


  1%|          | 16/2500 [00:00<00:32, 77.15it/s]


  1%|▏         | 32/2500 [00:00<00:23, 103.84it/s]


  2%|▏         | 48/2500 [00:00<00:21, 115.85it/s]


  3%|▎         | 64/2500 [00:00<00:19, 123.65it/s]


  3%|▎         | 80/2500 [00:00<00:18, 128.25it/s]


  4%|▎         | 93/2500 [00:00<00:18, 127.92it/s]


  4%|▍         | 109/2500 [00:00<00:18, 131.11it/s]


  5%|▌         | 125/2500 [00:00<00:17, 133.84it/s]


  6%|▌         | 140/2500 [00:01<00:17, 135.39it/s]


  6%|▌         | 156/2500 [00:01<00:17, 137.20it/s]


  7%|▋         | 171/2500 [00:01<00:16, 138.06it/s]


  7%|▋         | 187/2500 [00:01<00:16, 139.18it/s]


  8%|▊         | 202/2500 [00:01<00:16, 139.89it/s]


  9%|▊         | 218/2500 [00:01<00:16, 140.73it/s]


  9%|▉         | 233/2500 [00:01<00:16, 141.04it/s]


 10%|▉         | 249/2500 [00:01<00:15, 142.12it/s]


 11%|█         | 265/2500 [00:01<00:15, 142.73it/s]


 11%|█         | 281/2500 [00:01<00

Accuracy of the network on the 10000 test images: 74 %





  0%|          | 1/2500 [00:00<04:59,  8.35it/s]


  1%|          | 15/2500 [00:00<00:36, 67.93it/s]


  1%|          | 28/2500 [00:00<00:28, 85.99it/s]


  2%|▏         | 40/2500 [00:00<00:26, 93.80it/s]


  2%|▏         | 54/2500 [00:00<00:24, 101.26it/s]


  3%|▎         | 67/2500 [00:00<00:23, 105.36it/s]


  3%|▎         | 80/2500 [00:00<00:22, 108.46it/s]


  4%|▎         | 93/2500 [00:00<00:21, 110.85it/s]


  4%|▍         | 107/2500 [00:00<00:21, 113.31it/s]


  5%|▍         | 121/2500 [00:01<00:20, 115.41it/s]


  5%|▌         | 135/2500 [00:01<00:20, 117.28it/s]


  6%|▌         | 148/2500 [00:01<00:19, 118.27it/s]


  6%|▋         | 162/2500 [00:01<00:19, 119.58it/s]


  7%|▋         | 176/2500 [00:01<00:19, 120.53it/s]


  8%|▊         | 190/2500 [00:01<00:19, 120.08it/s]


  8%|▊         | 203/2500 [00:01<00:19, 120.63it/s]


  9%|▊         | 217/2500 [00:01<00:18, 121.28it/s]


  9%|▉         | 231/2500 [00:01<00:18, 121.95it/s]


 10%|▉         | 245/2500 [00:01<00:18

Accuracy of plane : 75 %
Accuracy of   car : 84 %
Accuracy of  bird : 67 %
Accuracy of   cat : 59 %
Accuracy of  deer : 75 %
Accuracy of   dog : 63 %
Accuracy of  frog : 82 %
Accuracy of horse : 72 %
Accuracy of  ship : 86 %
Accuracy of truck : 74 %
Finished Training


In [36]:
print("Epoch 11 to 15")
for epoch in range(10,15):  # loop over the dataset multiple times
    print('epoch ', epoch + 1)
    train(epoch, trainloader, optimizer, criterion)
    test(testloader, net)
    classwise_test(testloader, net)
    torch.save(net.state_dict(), './models/model-'+str(epoch)+'.pth')

print('Finished Training')




  0%|          | 0/12500 [00:00<?, ?it/s]

Epoch 11 to 15
epoch  11





  0%|          | 3/12500 [00:00<07:41, 27.10it/s]


  0%|          | 11/12500 [00:00<04:00, 51.84it/s]


  0%|          | 19/12500 [00:00<03:26, 60.49it/s]


  0%|          | 27/12500 [00:00<03:12, 64.93it/s]


  0%|          | 35/12500 [00:00<03:05, 67.11it/s]


  0%|          | 43/12500 [00:00<03:01, 68.55it/s]


  0%|          | 51/12500 [00:00<02:58, 69.77it/s]


  0%|          | 59/12500 [00:00<02:55, 70.82it/s]


  1%|          | 67/12500 [00:00<02:53, 71.63it/s]


  1%|          | 75/12500 [00:01<02:52, 72.14it/s]


  1%|          | 83/12500 [00:01<02:50, 72.71it/s]


  1%|          | 91/12500 [00:01<02:50, 72.80it/s]


  1%|          | 99/12500 [00:01<02:49, 73.29it/s]


  1%|          | 107/12500 [00:01<02:49, 73.17it/s]


  1%|          | 115/12500 [00:01<02:48, 73.59it/s]


  1%|          | 124/12500 [00:01<02:47, 74.06it/s]


  1%|          | 132/12500 [00:01<02:46, 74.36it/s]


  1%|          | 140/12500 [00:01<02:45, 74.52it/s]


  1%|          | 148/12500 [00:01<02:45

epoch 11 training loss: 0.237





  0%|          | 1/2500 [00:00<04:33,  9.15it/s]


  1%|          | 16/2500 [00:00<00:32, 75.70it/s]


  1%|▏         | 32/2500 [00:00<00:24, 101.46it/s]


  2%|▏         | 48/2500 [00:00<00:21, 114.14it/s]


  3%|▎         | 64/2500 [00:00<00:19, 122.04it/s]


  3%|▎         | 80/2500 [00:00<00:18, 127.89it/s]


  4%|▍         | 96/2500 [00:00<00:18, 131.42it/s]


  4%|▍         | 112/2500 [00:00<00:17, 134.56it/s]


  5%|▌         | 128/2500 [00:00<00:17, 136.78it/s]


  6%|▌         | 144/2500 [00:01<00:17, 138.16it/s]


  6%|▋         | 160/2500 [00:01<00:16, 139.54it/s]


  7%|▋         | 175/2500 [00:01<00:16, 137.61it/s]


  8%|▊         | 191/2500 [00:01<00:16, 139.09it/s]


  8%|▊         | 207/2500 [00:01<00:16, 140.11it/s]


  9%|▉         | 223/2500 [00:01<00:16, 141.13it/s]


 10%|▉         | 239/2500 [00:01<00:15, 141.91it/s]


 10%|█         | 255/2500 [00:01<00:15, 142.51it/s]


 11%|█         | 271/2500 [00:01<00:15, 143.07it/s]


 11%|█▏        | 287/2500 [00:01<00

...

epoch 15 training loss: 0.125





  0%|          | 2/2500 [00:00<02:17, 18.18it/s]


  0%|          | 12/2500 [00:00<00:46, 53.67it/s]


  1%|          | 19/2500 [00:00<00:42, 58.87it/s]


  1%|          | 26/2500 [00:00<00:40, 61.18it/s]


  1%|▏         | 33/2500 [00:00<00:39, 62.41it/s]


  2%|▏         | 45/2500 [00:00<00:34, 71.17it/s]


  2%|▏         | 58/2500 [00:00<00:31, 78.75it/s]


  3%|▎         | 73/2500 [00:00<00:27, 87.05it/s]


  4%|▎         | 89/2500 [00:00<00:25, 94.49it/s]


  4%|▍         | 105/2500 [00:01<00:23, 99.94it/s]


  5%|▍         | 120/2500 [00:01<00:22, 104.16it/s]


  5%|▌         | 136/2500 [00:01<00:21, 108.25it/s]


  6%|▌         | 151/2500 [00:01<00:21, 109.87it/s]


  7%|▋         | 165/2500 [00:01<00:21, 106.66it/s]


  7%|▋         | 177/2500 [00:01<00:22, 104.37it/s]


  8%|▊         | 188/2500 [00:01<00:22, 104.39it/s]


  8%|▊         | 202/2500 [00:01<00:21, 106.00it/s]


  9%|▊         | 216/2500 [00:02<00:21, 107.69it/s]


  9%|▉         | 232/2500 [00:02<00:20, 110.0

Accuracy of the network on the 10000 test images: 74 %





  0%|          | 1/2500 [00:00<05:55,  7.03it/s]


  0%|          | 12/2500 [00:00<00:51, 48.28it/s]


  1%|          | 23/2500 [00:00<00:38, 64.34it/s]


  1%|▏         | 32/2500 [00:00<00:36, 68.05it/s]


  2%|▏         | 39/2500 [00:00<00:37, 65.72it/s]


  2%|▏         | 46/2500 [00:00<00:38, 64.54it/s]


  2%|▏         | 52/2500 [00:00<00:38, 63.86it/s]


  2%|▏         | 61/2500 [00:00<00:36, 66.24it/s]


  3%|▎         | 72/2500 [00:01<00:34, 70.25it/s]


  3%|▎         | 84/2500 [00:01<00:32, 74.22it/s]


  4%|▍         | 98/2500 [00:01<00:30, 79.21it/s]


  4%|▍         | 110/2500 [00:01<00:29, 81.67it/s]


  5%|▍         | 121/2500 [00:01<00:29, 81.28it/s]


  5%|▌         | 131/2500 [00:01<00:29, 80.53it/s]


  6%|▌         | 140/2500 [00:01<00:29, 79.65it/s]


  6%|▌         | 151/2500 [00:01<00:28, 81.22it/s]


  7%|▋         | 164/2500 [00:01<00:27, 83.57it/s]


  7%|▋         | 178/2500 [00:02<00:26, 86.02it/s]


  8%|▊         | 191/2500 [00:02<00:26, 87.92it/s]


  

Accuracy of plane : 78 %
Accuracy of   car : 84 %
Accuracy of  bird : 72 %
Accuracy of   cat : 52 %
Accuracy of  deer : 74 %
Accuracy of   dog : 58 %
Accuracy of  frog : 78 %
Accuracy of horse : 70 %
Accuracy of  ship : 89 %
Accuracy of truck : 86 %
Finished Training
